In [87]:
import tensorflow as tf
import cv2
import numpy as np
import matplotlib.pyplot as plt
from keras.preprocessing.image import ImageDataGenerator
import os

In [88]:
from keras.utils import Sequence
from keras.layers import Conv2D, DepthwiseConv2D, SeparableConv2D
from keras.layers import BatchNormalization, ReLU, GlobalAveragePooling2D
from keras.models import Model
from keras.layers import Dense

In [89]:
train_data_dir=r"C:\Users\Acer\Desktop\Minor Project\Split\train"
img_size=128
batch_size=64

In [90]:
gpus = tf.config.list_physical_devices('GPU')
if gpus:
  try:
    # Currently, memory growth needs to be the same across GPUs
    for gpu in gpus:
      tf.config.experimental.set_memory_growth(gpu, True)
    logical_gpus = tf.config.list_logical_devices('GPU')
    print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
  except RuntimeError as e:
    # Memory growth must be set before GPUs have been initialized
    print(e)

1 Physical GPUs, 1 Logical GPUs


In [91]:
#os.environ["CUDA_VISIBLE_DEVICES"] = "1" 
#gpus = tf.config.experimental.list_physical_devices('GPU')
#if gpus:
   #for gpu in gpus:
      #tf.config.experimental.set_memory_growth(gpu, True)

In [92]:
class MergedGenerators(Sequence):
    def __init__(self, generators):
        self.generators = generators
        self.lengths = [len(gen) for gen in generators]
        self.cumulative_lengths = np.cumsum(self.lengths)

    def __len__(self):
        return self.cumulative_lengths[-1]

    def __getitem__(self, index):
        generator_index = np.argmax(index < self.cumulative_lengths)
        if generator_index > 0:
            sample_index = index - self.cumulative_lengths[generator_index - 1]
        else:
            sample_index = index

        # Get the data and labels from the corresponding generator
        data, labels = self.generators[generator_index][sample_index]
        return data, labels

In [93]:
normal_datagen = ImageDataGenerator(
    rescale=1.0 / 255,
)
noisy_datagen = ImageDataGenerator(
    rescale=1.0 / 255,
    preprocessing_function=lambda x: x + np.random.normal(0, 0.1, x.shape),  # Add noise
)
shaded_datagen = ImageDataGenerator(
    rescale=1.0 / 255,
    brightness_range=[0.5, 1.5],  # Adjust the range for shading
)
grayscale_datagen = ImageDataGenerator(
    rescale=1.0 / 255,
)

In [94]:
generator1 = normal_datagen.flow_from_directory(
    train_data_dir,
    target_size=(img_size,img_size),
    batch_size=batch_size,
    shuffle=True,
    seed=42,
    class_mode='categorical'
)
generator2 = shaded_datagen.flow_from_directory(
    train_data_dir,
    target_size=(img_size,img_size),
    batch_size=batch_size,
    shuffle=True,
    seed=42,
    class_mode='categorical'
)
generator3 = noisy_datagen.flow_from_directory(
    train_data_dir,
    target_size=(img_size,img_size),
    batch_size=batch_size,
    shuffle=True,
    seed=42,
    class_mode='categorical'
)
generator4 = grayscale_datagen.flow_from_directory(
    train_data_dir,
    target_size=(img_size,img_size),
    batch_size=batch_size,
    color_mode="grayscale",
    shuffle=True,
    seed=42,
    class_mode='categorical'
)

Found 8400 images belonging to 5 classes.
Found 8400 images belonging to 5 classes.
Found 8400 images belonging to 5 classes.
Found 8400 images belonging to 5 classes.


In [95]:
# Get a batch of images from the generator
batch_images, batch_labels = generator1.next()

# Set the number of images to display in each row
num_images_per_row = 10

# Calculate the number of rows needed
num_rows = int(len(batch_images) / num_images_per_row) + 1

# Display the images
fig, axes = plt.subplots(num_rows, num_images_per_row, figsize=(100, 100))

# Flatten the axes array if there is only one row
if num_rows == 1:
    axes = axes.reshape(1, -1)

for i in range(len(batch_images)):
    row_index = i // num_images_per_row
    col_index = i % num_images_per_row
    axes[row_index, col_index].imshow(batch_images[i])
    axes[row_index, col_index].axis('off')
plt.show()
    

In [96]:
combined_generator = MergedGenerators([generator1, generator2, generator3])

In [97]:
# Initialising the CNN
model = tf.keras.models.Sequential()

# Step 1 - Convolution
model.add(tf.keras.layers.Conv2D(filters=32, kernel_size=3, activation='relu', input_shape=[img_size, img_size, 3]))
# model.add(tf.keras.layers.BatchNormalization())

# Step 2 - Pooling
model.add(tf.keras.layers.MaxPool2D(pool_size=2, strides=2))
# model.add(tf.keras.layers.BatchNormalization())

# Adding a second convolutional layer
model.add(tf.keras.layers.Conv2D(filters=32, kernel_size=3, activation='relu'))
model.add(tf.keras.layers.MaxPool2D(pool_size=2, strides=2))
# model.add(tf.keras.layers.BatchNormalization())

# Step 3 - Flattening
model.add(tf.keras.layers.Flatten())
# model.add(tf.keras.layers.BatchNormalization())

# Step 4 - Full Connection
model.add(tf.keras.layers.Dense(units=128, activation='relu'))
# model.add(tf.keras.layers.BatchNormalization())

# Step 5 - Output Layer
model.add(tf.keras.layers.Dense(units=5, activation='softmax'))


In [98]:
# lr_schedule = tf.keras.optimizers.schedules.ExponentialDecay(
#                 initial_learning_rate = 1e-3,
#                 decay_steps = 10000,
#                 decay_rate = 0.9)
optimizer = tf.keras.optimizers.Adam(learning_rate = 0.001)
model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])


In [99]:
test_data_dir=r"C:\Users\Acer\Desktop\Minor Project\Split\val"
test_datagen = ImageDataGenerator(rescale = 1.0/255)

test_generator = test_datagen.flow_from_directory(test_data_dir,
                                                  target_size=(img_size, img_size),
                                                  batch_size=batch_size,
                                                  class_mode='categorical')

Found 2400 images belonging to 5 classes.


In [100]:

history = model.fit(combined_generator, epochs=5, validation_data=test_generator)


Epoch 1/5
396/396 [==============================] - 112s 281ms/step - loss: 0.4470 - accuracy: 0.8348 - val_loss: 0.1093 - val_accuracy: 0.9683
Epoch 2/5
396/396 [==============================] - 96s 243ms/step - loss: 0.0501 - accuracy: 0.9852 - val_loss: 0.0671 - val_accuracy: 0.9800
Epoch 3/5
396/396 [==============================] - 98s 247ms/step - loss: 0.0154 - accuracy: 0.9965 - val_loss: 0.0725 - val_accuracy: 0.9800
Epoch 4/5
396/396 [==============================] - 97s 244ms/step - loss: 0.0078 - accuracy: 0.9983 - val_loss: 0.0972 - val_accuracy: 0.9688
Epoch 5/5
396/396 [==============================] - 96s 241ms/step - loss: 0.0367 - accuracy: 0.9892 - val_loss: 0.1121 - val_accuracy: 0.9683
